# オブジェクト指向回
リファクタリング後のコード

## キャンペーンと継承の話

In [ ]:
from typing import final
from typing_extensions import override

In [ ]:
class Campaign:
    "キャンペーン"

    def get_discounted_price(self, price: int):
        "割引後の価格を計算する"
        raise NotImplementedError()

    @final
    def compute_discounted_amount(self, price: int):
        "割引された額を計算する"
        return price - self.get_discounted_price(price)


class RateDiscountCampaign(Campaign):
    "割引キャンペーン"

    def __init__(self, discount_rate: float):
        super().__init__()

        self.__discount_rate = discount_rate

    @override
    def get_discounted_price(self, price: int):
        return int(price * (1 - self.__discount_rate))


class ValueDiscountCampaign(Campaign):
    "固定値値引きキャンペーン"

    def __init__(self, discount_value: float):
        super().__init__()

        self.__discount_value = discount_value

    @override
    def get_discounted_price(self, price: int):
        return price - self.__discount_value


class Subscription:
    "申込"

    def __init__(self, plan_id: int, price: int, campaign: Campaign):
        self.__plan_id = plan_id
        self.__monthly_price = price
        self.__campaign = campaign

    def plan_id(self):
        return self.__plan_id

    def monthly_price(self):
        "割引後の価格を計算する"
        return self.__campaign.get_discounted_price(self.__monthly_price)

    def compute_discounted_amount(self):
        "割引される額を計算する"
        return self.__campaign.compute_discounted_amount(self.__monthly_price)




In [ ]:
sub = Subscription(
    plan_id=12345,
    price=1000,  # 1000円のプランを購読
    campaign=RateDiscountCampaign(0.2),  # 20% OFF
)
print(sub.monthly_price())  # => 800円
print(sub.compute_discounted_amount())  # => 200円

sub = Subscription(
    plan_id=12345,
    price=1000,  # 1000円のプランを購読
    campaign=ValueDiscountCampaign(300),  # 300円引き
)
print(sub.monthly_price())  # => 700円
print(sub.compute_discounted_amount())  # => 300円



800
200
700
300


## メール送信とインターフェースの話

In [ ]:
from abc import ABC, abstractmethod


In [ ]:
def get_price(plan_id: int) -> int:
    # 本当は価格を取得する処理
    return 1000


def get_campaign() -> Campaign:
    return RateDiscountCampaign(0.2)


def save_to_database(subscription: Subscription):
    # 本当は保存処理
    pass


class MailClient(ABC):
    @abstractmethod
    def send_mail_to(self, address: str, message: str):
        "メール送信処理"
        pass


# 本番環境用
class ActualMailClient(MailClient):
    @override
    def send_mail_to(self, address: str, message: str):
        # 本当はメール送信処理、例示のため print() で代用しておく
        print("actually send mail")
        pass


def subscribe(mail_client: MailClient, mail_address: str, plan_id: int):
    "申し込む"

    # なんやかんやプラン情報を取得して
    price = get_price(plan_id)
    campaign = get_campaign()
    subscription = Subscription(plan_id, price, campaign=campaign)

    # 申込情報をデータベースに保存
    save_to_database(subscription)

    # メール送信
    message = f"{subscription.monthly_price()}円で購読ありがとうございます"
    mail_client.send_mail_to(mail_address, message)




In [ ]:
# 本番
subscribe(ActualMailClient(), "test@example.com", 12345)


actually send mail


### テスト用

In [ ]:
class MockMailClient(MailClient):
    @override
    def send_mail_to(self, address: str, message: str):
        # テスト用なので、メール送信をしない
        print("送信しました")


In [ ]:
subscribe(MockMailClient(), "test@example.com", 12345)

送信しました
